In [2]:
import numpy as np
import pandas as pd
import networkx as nx
import plotly.io as pio
import plotly.express as px
import plotly.graph_objects as go
import igviz as ig
from node2vec import Node2Vec
from gensim.models import KeyedVectors
import seaborn as sns
import matplotlib.pyplot as plt
# import src.visualize as vis
# from src.visualize import visualize_celllevel_graph
# # import sys
# sys.path.append('./src/')
# sys.path.append('./src/submodules/CeSpGRN/src/')
# from src.preprocessing import construct_celllevel_graph
from plotly.subplots import make_subplots
# from src import models, training
# from torch_geometric.nn import GAE
import torch
import os
from plotly.offline import plot, iplot, init_notebook_mode
from sklearn.model_selection import train_test_split

raw_data_path = "./data/"
starting_df = pd.read_csv(os.path.join(raw_data_path,f"seqfish_dataframe.csv"))

In [3]:
import plotly.graph_objects as go
import plotly.express as px

def visualize_celllevel_graph(df, gene, title, edge_trace=None, publication=False):
    fig = px.scatter(df, x="X", y="Y", custom_data=["Cell_ID"], color=gene, width=700, height=650,
                     color_continuous_scale="Viridis", title=title)  # 颜色选用Viridis或者其他更简洁的配色方案

    # 如果有边的坐标，添加边的描绘
    if edge_trace is not None:
        fig.add_trace(go.Scatter(
            x=edge_trace[0], y=edge_trace[1],
            line=dict(width=0.4, color='#888'),
            hoverinfo='none',
            mode='lines', name="Edges"))

    # 更新点的显示样式
    fig.update_traces(
        hovertemplate="<br>".join([
            "Cell_ID: %{customdata[0]}",
            "X: %{x}",
            "Y: %{y}",
        ]),
        marker=dict(
            size=6,  # 点的大小，适中
            color='gray',  # 使用灰色的点
            opacity=0.8,  # 设置透明度
            line=dict(width=0)  # 去掉点的边框
        )
    )

    # 设置不出版的布局样式
    if not publication:
        fig.update_layout(coloraxis_colorbar=dict(yanchor="top", y=1, x=-0.2))

        # 隐藏网格线和轴线背景
        fig.update_xaxes(showline=False, linewidth=2, linecolor='rgba(1,1,1,0)', gridcolor='rgba(1,1,1,0)', zeroline=False)
        fig.update_yaxes(showline=False, linewidth=2, linecolor='rgba(1,1,1,0)', gridcolor='rgba(1,1,1,0)', zeroline=False)

    # 设置出版风格的布局（清晰的白色背景，简洁的线条，去除不必要的元素）
    fig.update_layout(
        title=title,
        title_x=0.5,
        title_font=dict(size=24, family="Times New Roman", color="black"),  # 更简洁的字体风格
        plot_bgcolor="white",  # 设为白色背景
        paper_bgcolor="white",  # 设为白色背景
        font=dict(family="Times New Roman", color="black", size=16),  # 设置字体
        margin=dict(t=50, b=50, l=50, r=50),  # 留出适当的边距
        showlegend=False,  # 去除图例
        xaxis=dict(showline=True, linewidth=1, linecolor='black', ticks='outside', tickwidth=1, ticklen=5),
        yaxis=dict(showline=True, linewidth=1, linecolor='black', ticks='outside', tickwidth=1, ticklen=5),
    )

    # 删除颜色轴（如果不需要）
    fig.update_coloraxes(showscale=False)

    return fig




In [5]:
import numpy as np
import pandas as pd

def construct_celllevel_graph_with_gaussian_kernel(data_df, k, sigma=10.0, tau=0.5, get_edges=False):
    '''
    Constructs a new cell graph with spatial proximity edges based on Gaussian kernel weights.

    :data_df: pd.DataFrame : represents the spatial data and contains the following columns ["Cell_ID", "X", "Y"]
    :k: int : Number of nearest neighbors to construct spatial edges for
    :sigma: float : Standard deviation for the Gaussian kernel (controls the range of influence)
    :tau: float : Threshold for the weight matrix to define biologically meaningful interactions
    :get_edges: boolean : True to return edge_trace (for visualization purposes)

    :return: Cell_level_adjacency, edge list
    '''

    # Initialize adjacency matrix and edge lists
    adjacency = np.zeros(shape=(len(data_df), k), dtype=int)  # shape = (num_cells, num_neighbors)
    coords = np.vstack([data_df["X"].values, data_df["Y"].values]).T  # Cell coordinates

    edges = None
    edge_x = []
    edge_y = []

    for i in range(len(data_df)):  # Loop through each cell
        x0, y0 = data_df["X"].values[i], data_df["Y"].values[i]
        candidate_cell = coords[i]
        candidate_neighbors = coords
        euclidean_distances = np.linalg.norm(candidate_neighbors - candidate_cell, axis=1)

        # Step 1: Compute the Gaussian kernel weights for all cells (instead of just neighbors)
        gaussian_weights = np.exp(-euclidean_distances**2 / (2 * sigma**2))
        
        # Step 2: Sort cells based on Gaussian weights in descending order (ignore self)
        sorted_indices = np.argsort(gaussian_weights)[::-1]  # Sort by weight (descending)
        sorted_indices = sorted_indices[sorted_indices != i]  # Exclude self (index i)
        
        # Step 3: Apply threshold tau and select up to k neighbors
        valid_neighbors = [idx for idx in sorted_indices if gaussian_weights[idx] >= tau][:k]
        
        # Fill adjacency list with valid neighbors
        adjacency[i, :len(valid_neighbors)] = valid_neighbors
        
        if get_edges:
            for ncell in valid_neighbors:
                x1, y1 = data_df["X"].values[ncell], data_df["Y"].values[ncell]
                edge_x.append(x0)
                edge_x.append(x1)
                edge_x.append(None)
                edge_y.append(y0)
                edge_y.append(y1)
                edge_y.append(None)

    # Return adjacency matrix and edge trace (for visualization)
    edges = [edge_x, edge_y] if get_edges else None

    return adjacency, edges

starting_df = pd.read_csv(os.path.join(raw_data_path,f"seqfish_dataframe.csv"))
# 使用该函数构建细胞互作网络
celllevel_adj1, edges1 = construct_celllevel_graph_with_gaussian_kernel(
    starting_df, k=5, sigma=100, tau=0.05, get_edges=True
)

# 使用可视化函数显示结果
sim_fig = visualize_celllevel_graph(
    starting_df, gene="X", title="Cell_Interaction_Knn(Gaussian)", edge_trace=edges1, publication=True
)

sim_fig.show()


In [9]:
from sklearn.cluster import AgglomerativeClustering
import numpy as np
import pandas as pd
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.cluster import KMeans
import matplotlib.pyplot as plt
def construct_celllevel_graph_with_hierarchical_clustering(data_df, k=5, threshold=0.5, n_clusters=10, max_distance=5000, return_edges=False):
    """
    基于基因表达相似度和空间距离限制构建 kNN 初始网络，并使用层次聚类进行优化。

    参数:
    - data_df (pd.DataFrame): 包含细胞的特征矩阵，必须包含 ["Cell_ID", "X", "Y"] 和基因表达列。
    - k (int): 每个细胞保留的最近邻数量。
    - threshold (float): 基因相似度阈值 (0 < threshold <= 1)。
    - n_clusters (int): KMeans聚类的聚类数。
    - max_distance (float): 细胞间的最大空间距离，用于限制聚类范围。
    - return_edges (bool): 是否返回优化后的边，用于可视化。

    返回:
    - optimized_adjacency (np.array): 优化后的邻接矩阵。
    - edges (list or None): 边的坐标列表（用于可视化），如果 return_edges=True。
    """
    # **1. 数据预处理**
    feature_df = data_df.drop(columns=["Cell_ID", "X", "Y", "Cell_Type"], errors='ignore')
    feature_df = feature_df.select_dtypes(include=[np.number])
    feature_matrix = feature_df.values  # 转换为 NumPy 矩阵
    
    num_cells = len(data_df)
    
    # **2. 计算细胞之间的余弦相似度**
    similarity_matrix = cosine_similarity(feature_matrix)
    
    # **3. 计算细胞之间的空间距离 (Euclidean Distance)**
    x_coords = data_df['X'].values
    y_coords = data_df['Y'].values
    spatial_distance_matrix = np.sqrt((x_coords[:, None] - x_coords)**2 + (y_coords[:, None] - y_coords)**2)
    
    # **4. 构建 kNN 初始网络**
    adjacency = np.zeros((num_cells, num_cells), dtype=int)
    for i in range(num_cells):
        similarities = similarity_matrix[i].copy()
        similarities[i] = -1  # 排除自身
        
        # 筛选满足基因相似度阈值的邻居
        valid_neighbors = np.where(similarities >= threshold)[0]
        
        # 只考虑在最大距离范围内的细胞
        valid_neighbors = [n for n in valid_neighbors if spatial_distance_matrix[i, n] <= max_distance]
        
        # 对有效邻居按照相似度进行排序
        if len(valid_neighbors) < k:
            neighbors = valid_neighbors
        else:
            # 获取相似度最高的k个邻居
            sorted_neighbors = np.argsort(similarities[valid_neighbors])[-k:]
            neighbors = np.array(valid_neighbors)[sorted_neighbors]
        
        # 更新邻接矩阵
        for ncell in neighbors:
            adjacency[i, ncell] = 1
            adjacency[ncell, i] = 1  # 无向图
    
    print(f"Initial edges count: {adjacency.sum() // 2}")
    
    # **5. 使用层次聚类进行空间聚类**
    hierarchical = AgglomerativeClustering(n_clusters=n_clusters, linkage='ward')
    cluster_labels = hierarchical.fit_predict(np.column_stack([x_coords, y_coords]))
    
    # 将聚类结果添加到数据框中
    data_df['Cluster_Label'] = cluster_labels
    
    print(f"Number of clusters detected: {len(set(cluster_labels))}")
    
    # **6. 使用kNN和空间聚类交集优化邻接矩阵**
    optimized_adjacency = np.zeros_like(adjacency)
    for i in range(num_cells):
        for j in range(i + 1, num_cells):
            # 如果两细胞在同一聚类内，且属于kNN邻接关系，则认为它们是互作关系
            if adjacency[i, j] == 1 and cluster_labels[i] == cluster_labels[j]:
                optimized_adjacency[i, j] = 1
                optimized_adjacency[j, i] = 1  # 无向图

    # 如果需要返回优化后的边（用于可视化）
    if return_edges:
        edge_x, edge_y = [], []
        for i in range(num_cells):
            for j in range(i + 1, num_cells):
                if optimized_adjacency[i, j] == 1:  # 如果这对细胞属于同一聚类并有kNN关系
                    x0, y0 = data_df["X"].values[i], data_df["Y"].values[i]
                    x1, y1 = data_df["X"].values[j], data_df["Y"].values[j]
                    edge_x.extend([x0, x1, None])
                    edge_y.extend([y0, y1, None])

        edges = [edge_x, edge_y]
    else:
        edges = None
    
    return optimized_adjacency, edges, data_df



starting_df = pd.read_csv(os.path.join(raw_data_path,f"seqfish_dataframe.csv"))
celllevel_adj2, edges2, updated_data_df = construct_celllevel_graph_with_hierarchical_clustering(
    data_df=starting_df,
    k=20,
    threshold=0.4,
    n_clusters=7,
    max_distance=10000,  
    return_edges=True  # 设置为 True 来返回边的坐标
)

# 查看聚类标签
print(updated_data_df[['Cell_ID', 'Cluster_Label']].head())

# 可视化优化后的细胞互作网络
sim_fig_optimized = visualize_celllevel_graph(
    starting_df, gene="X", title="Cell_Interaction_Similarity(AgglomerativeClustering)", edge_trace=edges, publication=True
)

sim_fig_optimized.show()


Initial edges count: 1225
Number of clusters detected: 7
   Cell_ID  Cluster_Label
0        1              5
1        2              5
2        3              5
3        4              5
4        5              5


In [10]:
import numpy as np
import pandas as pd

def compute_dynamic_distance_threshold(ligand_val, receptor_val, min_distance=1000, max_distance=5000, scale_factor=100):
    """
    基于配体和受体表达值计算动态的空间距离阈值
    :param ligand_val: 配体的表达值
    :param receptor_val: 受体的表达值
    :param min_distance: 最小空间距离
    :param max_distance: 最大空间距离
    :param scale_factor: 表达值影响的系数
    :return: 动态的空间距离阈值
    """
    expr_diff = abs(ligand_val - receptor_val)
    # 使用表达值差异来缩放距离阈值
    dynamic_threshold = max(min_distance, max_distance - expr_diff * scale_factor)
    return dynamic_threshold

def compute_similarity_weighted_strength(interaction_strength, feature_similarity, alpha=0.5):
    """
    计算加权的配体-受体相互作用强度，考虑空间和基因表达的相似度
    :param interaction_strength: 配体-受体的原始相互作用强度
    :param feature_similarity: 特征相似度矩阵（如基因表达相似度）
    :param alpha: 空间相似度与特征相似度的权重系数
    :return: 加权后的相互作用强度
    """
    return alpha * interaction_strength + (1 - alpha) * feature_similarity

def construct_celllevel_graph_with_dynamic_threshold_and_weights(data_df, ligand="Gdf5", receptor="Bmpr1b", 
                                                                k=5, threshold=0.5, distance_threshold=10, 
                                                                alpha=0.5, get_edges=True):
    """
    基于配体和受体的表达值、空间距离、以及基因表达相似度，构建细胞图，保留每个细胞的前 k 个相似度最高且大于等于阈值的边。
    """
    # 提取配体和受体的表达值
    L_vals = data_df[ligand].values
    R_vals = data_df[receptor].values
    
    # 计算配体和受体之间的外积 (interaction strength)
    interaction_strength_matrix = np.outer(L_vals, R_vals)
    
    # 计算细胞之间的空间距离 (Euclidean Distance)
    x_coords = data_df['X'].values
    y_coords = data_df['Y'].values
    spatial_distance_matrix = np.sqrt((x_coords[:, None] - x_coords)**2 + (y_coords[:, None] - y_coords)**2)
    
    # 计算基因表达相似度（例如，可以使用皮尔逊相关系数或余弦相似度）
    feature_df = data_df.drop(columns=["Cell_ID", "X", "Y", "Cell_Type"], errors='ignore')
    feature_df = feature_df.select_dtypes(include=[np.number])
    feature_matrix = feature_df.values
    gene_similarity_matrix = cosine_similarity(feature_matrix)  # 使用余弦相似度
    
    num_cells = len(data_df)
    adjacency = -1 * np.ones((num_cells, k), dtype=int)
    
    edge_x, edge_y = [], []
    
    for i in range(num_cells):
        strengths = interaction_strength_matrix[i].copy()
        strengths[i] = -1  # 排除自身
        
        # 1) 计算布尔掩码: 强度 >= threshold
        valid_mask_strength = (strengths >= threshold)
        
        # 2) 计算布尔掩码: 距离 >= distance_threshold
        dist_row = spatial_distance_matrix[i]
        valid_mask_distance = (dist_row >= distance_threshold)
        
        # 3) 两个条件同时满足
        combined_mask = valid_mask_strength & valid_mask_distance
        
        # 4) 找到满足条件的邻居
        valid_neighbors = np.where(combined_mask)[0]  
        valid_strengths = strengths[valid_neighbors]
        
        # 若满足条件的邻居数大于 k，则只取强度最高的 k 个
        if len(valid_neighbors) > k:
            # 对配体-受体相互作用强度与基因相似度进行加权
            weighted_strengths = []
            for neighbor in valid_neighbors:
                # 计算相似度加权
                feature_similarity = gene_similarity_matrix[i, neighbor]  # 基因相似度
                weighted_strength = compute_similarity_weighted_strength(strengths[neighbor], feature_similarity, alpha)
                weighted_strengths.append(weighted_strength)
            
            weighted_strengths = np.array(weighted_strengths)
            top_k_indices = np.argsort(weighted_strengths)[-k:]  # 最强的 k 个
            neighbors = valid_neighbors[top_k_indices]
        else:
            neighbors = valid_neighbors
        
        # 更新邻接矩阵（只记录邻居索引）
        adjacency[i, :len(neighbors)] = neighbors
        
        # 如果需要边的可视化
        if get_edges:
            x0, y0 = data_df.loc[i, ["X", "Y"]]
            for ncell in neighbors:
                x1, y1 = data_df.loc[ncell, ["X", "Y"]]
                edge_x.extend([x0, x1, None])
                edge_y.extend([y0, y1, None])
    
    edges = [edge_x, edge_y] if get_edges else None
    return adjacency, edges

# 使用改进的函数构建带有动态阈值和加权边的细胞图

starting_df = pd.read_csv(os.path.join(raw_data_path, "seqfish_dataframe.csv"))

# 构建细胞图
celllevel_adj3, edges3 = construct_celllevel_graph_with_dynamic_threshold_and_weights(
    starting_df, 
    ligand="Gdf5", 
    receptor="Bmpr1b", 
    k=5, 
    threshold=5,  # 配体-受体相互作用强度阈值
    distance_threshold=3000,  # 空间距离阈值
    alpha=0.5,  # 空间相似度与基因相似度的加权系数
    get_edges=True
)

# 可视化细胞间互作网络
sim_fig = visualize_celllevel_graph(starting_df, gene="X", title="Cell_Interaction_LR（joint filtering）", edge_trace=edges3, publication=True)
sim_fig.show()


In [12]:


import numpy as np
def merge_adjacency_lists_with_edges_limited_k(adj_lists, data_df, k=10, get_edges=True):
    """
    合并多个邻接列表，取并集，并限制每个细胞的邻接数为 k，返回邻接矩阵和边的坐标。
    :param adj_lists: list of adjacency lists : 输入的邻接列表集合
    :param data_df: pd.DataFrame : 代表空间数据，包含 ["Cell_ID", "X", "Y"] 和其他特征列
    :param k: int : 每个细胞最多保留 k 个邻居
    :param get_edges: boolean : 是否返回边的坐标（用于可视化）
    :return: adjacency (2D array), edges (optional)
    """
    # 初始化一个空集合，避免重复的边
    merged_edges = set()
    num_cells = len(data_df)    
    # 初始化邻接字典（用于临时存储邻居索引）
    temp_adjacency = {i: set() for i in range(num_cells)}  # 用集合去重
    edge_x, edge_y = [], []
    # 遍历所有输入的邻接列表
    for adj in adj_lists:
        for i, neighbors in enumerate(adj):
            for j in neighbors:
                if i < j and (i, j) not in merged_edges:  # 确保边唯一且无向
                    merged_edges.add((i, j))
                    temp_adjacency[i].add(j)
                    temp_adjacency[j].add(i)  # 无向图
                    # 如果需要边的坐标
                    if get_edges:
                        x0, y0 = data_df.loc[i, ["X", "Y"]]
                        x1, y1 = data_df.loc[j, ["X", "Y"]]
                        edge_x.extend([x0, x1, None])
                        edge_y.extend([y0, y1, None])
    # 限制邻接矩阵为固定维度 k
    adjacency = np.zeros((num_cells, k), dtype=int)  # 初始化邻接矩阵
    for i in range(num_cells):
        neighbors = list(temp_adjacency[i])  # 获取邻居索引列表
        if len(neighbors) > k:
            neighbors = neighbors[:k]  # 截断为前 k 个邻居
        adjacency[i, :len(neighbors)] = neighbors  # 填充到邻接矩阵
    edges = [edge_x, edge_y] if get_edges else None
    return adjacency, edges


# 合并邻接列表，并获取邻接列表和边坐标
adj_lists = [celllevel_adj1,celllevel_adj2, celllevel_adj3]
celllevel_adj4, edges4 = merge_adjacency_lists_with_edges_limited_k(adj_lists, starting_df, k=30,get_edges=True)

sim_fig = visualize_celllevel_graph(starting_df, gene="X", title="Cell_Interaction_Refine(Seqfish)", edge_trace=edges4, publication=True)




sim_fig.show()

In [14]:
def construct_celllevel_graph(data_df, k, get_edges=False):   # Top k closest neighbors for each cell
    '''
    Constructs new cell graph with spatial proximity edges based on kNN.
    
    :data_df: pd.DataFrame : represents the spatial data and contains the following columns ["Cell_ID", "X", "Y"]
    :k: int: Number of nearest neighbors to construct spatial edges for
    :get_edges: boolean:  True to return edge_trace (for visualization purposes)
    
    :return: Cell_level_adjacency, edge list
    '''
    
    adjacency = np.zeros(shape=(len(data_df), k), dtype=int)  # shape = (numcells, numneighbors of cell)
    coords = np.vstack([data_df["X"].values, data_df["Y"].values]).T

    edges = None
    edge_x = []
    edge_y = []

    for i in range(len(data_df)):  # Standard for loop for processing
        cell_id = data_df["Cell_ID"][i]
        x0, y0 = data_df["X"].values[i], data_df["Y"].values[i]
        candidate_cell = coords[i]
        candidate_neighbors = coords
        euclidean_distances = np.linalg.norm(candidate_neighbors - candidate_cell, axis=1)
        neighbors = np.argsort(euclidean_distances)[1:k+1]  # Exclude self (distance 0)
        adjacency[i] = neighbors
        assert i not in adjacency[i], f"Self-loop detected for cell {i}."
        if get_edges:
            for ncell in adjacency[i]:
                x1, y1 = data_df["X"].values[ncell], data_df["Y"].values[ncell]
                edge_x.append(x0)
                edge_x.append(x1)
                edge_x.append(None)
                edge_y.append(y0)
                edge_y.append(y1)
                edge_y.append(None)
        
    edges = [edge_x, edge_y] if get_edges else None
                
    return adjacency, edges
starting_df = pd.read_csv(os.path.join(raw_data_path,f"seqfish_dataframe.csv"))
celllevel_adj1, edges1 = construct_celllevel_graph(starting_df, 5, get_edges=True)
# 使用函数可视化
sim_fig = visualize_celllevel_graph(starting_df, gene="X", title="Cell_Interaction_Clarify(Seqfish)", edge_trace=edges1, publication=True)


sim_fig.show()